# Get all revisions that are redirects

For a given wiki we want to find all revisions that are redirects.
We query [wmf.mediawiki_wikitext_history](https://wikitech.wikimedia.org/wiki/Analytics/Data_Lake/Content/XMLDumps/Mediawiki_wikitext_history).

How:
- get all redirect-aliases
    - for any wiki we can extract all redirect-aliases from '%s-latest-siteinfo-namespaces.json.gz'
- query all revision-ids that are redirects
    - we look at the column 'revision_text'
    - we check whether the it starts with the string '#redirect [[*]]' or any of its aliases using sql's LIKE command
    - we only consider lower-case strings (syntax agnostic to capitalization)
- regexp-extract to get redirect-page from text-field

In [1]:
import os
from pyspark.sql.functions import  col,regexp_extract ## for extracting redirect-page
from redirect import get_redirect_aliases ## for getting redirect-aliases

In [2]:
## select the wmf table
sqlContext.sql('USE wmf')

DataFrame[]

## Which wiki

In [3]:
wiki_date = '2019-07'
wiki_name = 'rowiki'


## Get all redirect - aliases

In [4]:
## we look up the json of the latest siteinfo-namespaces file
filename = os.path.join('/mnt','data','xmldatadumps','public','%s'%wiki_name,'latest','%s-latest-siteinfo-namespaces.json.gz'%wiki_name)
list_redirect_aliases = get_redirect_aliases(filename)
print(list_redirect_aliases)


['#REDIRECT', '#REDIRECTEAZA']


## Query


In [5]:
## construct the string-matching condition
str_revision_redirect_match = '('
for i_redirect_alias, redirect_alias in enumerate(list_redirect_aliases):
    if i_redirect_alias > 0:
        str_revision_redirect_match += ' OR '
    str_revision_redirect_match += 'LOWER(revision_text) LIKE "%s [[%%]]%%"'%(redirect_alias.lower())
str_revision_redirect_match += ')'
print(str_revision_redirect_match)

(LOWER(revision_text) LIKE "#redirect [[%]]%" OR LOWER(revision_text) LIKE "#redirecteaza [[%]]%")


In [10]:
## query all revision which start with '#redirect [[*]]' or one of its redirect-aliases

query = 'SELECT page_id, revision_id, page_title, revision_text \
FROM wmf.mediawiki_wikitext_history \
WHERE snapshot="%s" \
AND wiki_db="%s" \
AND page_namespace = 0 \
AND %s \
ORDER BY page_id, revision_id \
'\
%(wiki_date,wiki_name,str_revision_redirect_match)
print(query)

result = sqlContext.sql(query)

## extracting the page [[ ]] where it redirects to
## drop the revision-text (too much information)

df_final = result.withColumn('revision_redirect_page',regexp_extract(col('revision_text'), '\[\[(.*?)\]\]',1  ) )\
.drop('revision_text')\
.toPandas()



SELECT page_id, revision_id, page_title, revision_text FROM wmf.mediawiki_wikitext_history WHERE snapshot="2019-07" AND wiki_db="rowiki" AND page_namespace = 0 AND (LOWER(revision_text) LIKE "#redirect [[%]]%" OR LOWER(revision_text) LIKE "#redirecteaza [[%]]%") ORDER BY page_id, revision_id 


In [11]:
## save result to csv-dataframe
df_final.to_csv(df_redirect_revision_%s.csv'%wiki_name)

In [12]:
df_final

page_id  revision_id                                      page_title  \
0             9        66798                                          Fizica   
1             9      1303010                                          Fizica   
2             9      1705699                                          Fizica   
3             9      2126089                                          Fizica   
4             9      5693014                                          Fizica   
5             9     10723388                                          Fizica   
6            13         1962                                           Limbi   
7            13        66801                                           Limbi   
8            13      3020259                                           Limbi   
9            13      3914562                                           Limbi   
10           13      8881133                                           Limbi   
11           14        66802                                     Lingvistica   
12           15        66803                                    Limba romana   
13           17        66805                                   Arte martiale   
14           17       232040                                   Arte martiale   
15           17      4622678                                   Arte martiale   
16           17     12196093                                   Arte martiale   
17           17     12206268                                   Arte martiale   
18           24        66811                        Romania (dezambiguizare)   
19           24       747673                        Romania (dezambiguizare)   
20           24       748034                        Romania (dezambiguizare)   
21           49        66833                                         Religii   
22           71      2461256                                   GPL (licență)   
23           71      2896707                                   GPL (licență)   
24           71      2896715                                   GPL (licență)   
25           71      2986782                                   GPL (licență)   
26           71      4044515                                   GPL (licență)   
27           71      4184309                                   GPL (licență)   
28           76        66859                                    Limba valonă   
29           80        66862                                        Nazismul   
...         ...          ...                                             ...   
424323  2423632     12985859                                    Crinul tigru   
424324  2423754     12986164                          Reclamă de Televiziune   
424325  2423877     12986435  Nomenclatorul drumurilor naționale din România   
424326  2423919     12986606                                         NGC 242   
424327  2423921     12986619                               Iacob I de Aragon   
424328  2423972     12986802                                            DN 5   
424329  2424061     12987400                            After School (grupă)   
424330  2424071     12987453                            Lactarius deterrimus   
424331  2424153     12987875                               Dumbo (povestiri)   
424332  2424173     12988014                               Liudmila Saveleva   
424333  2424181     12988040                 Reeducarea în România Comunistă   
424334  2424230     12988331                                 James B. Conant   
424335  2424236     12988655                             Dirijor Mircea Popa   
424336  2424257     12989799                              Nürburg (Gemeinde)   
424337  2424323     12990052                                        Hachioji   
424338  2424380     12992295                               Procedeu Edeleanu   
424339  2424381     12992303                                Procedeu Leblanc   
424340  2424385     12992662                                     Vasile Șova   
424341  